In [1]:
#!pip install pandas-profiling[notebook] --quiet
#!pip install pydicom --quiet
#!pip install plotly --quiet
#!pip install fastprogress --quiet

import matplotlib.pyplot as plt 
import matplotlib.patches as patches
import numpy as np 
import os 
import pandas as pd 
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio
import pydicom as dicom
import seaborn as sns
import tensorflow as tf

from keras.regularizers import l2
from keras.models import Sequential
from keras.layers import Dropout, Dense
from mpl_toolkits.mplot3d import Axes3D
from pandas_profiling import ProfileReport
from PIL import Image
from fastprogress import progress_bar
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from tensorflow import keras
from tensorflow.keras import layers
from keras.regularizers import l2
from datetime import datetime
from IPython.display import Image


PURCHASE_CSV_PATH = "data/transactions_2018.csv"
PURCHASE_CSV_PATH_2 = "data/transactions_2017.csv"
CLIENT_CSV_PATH = "data/cardholder_info.csv"
PRODUCT_CSV_PATH = "data/merchant_info.csv" 
#JSONS_DIR = "../tmp/jsons/"

BASE_SPLIT_POINT = datetime.strptime('Feb 1 2018  1:33PM', '%b %d %Y %I:%M%p')

In [2]:
dfMerchant = pd.read_csv(PRODUCT_CSV_PATH)
dfTrx2018 = pd.read_csv(PURCHASE_CSV_PATH)
dfTrx2017 = pd.read_csv(PURCHASE_CSV_PATH_2)
dfTrx = pd.concat([dfTrx2017, dfTrx2018])
dfChd = pd.read_csv(CLIENT_CSV_PATH)

# Project Goals
* learn about recommender systems => will be used for capstone project
* work with similar dataset to PROD
* implemented rough content based/and item to item CF


In [3]:
Image(url='https://miro.medium.com/max/3630/1*rCK9VjrPgpHUvSNYw7qcuQ@2x.png')

## Data & data representation
* mini data set from Credit card transactions - > 2017/2018
* relatively clean and restricted (no charge back, no PIN reset, no empty MCC)
* source - course on Dataiku (from Jay Narhan)

Normally RS are perceived as user to item interaction. In my case I worked with credit card data. So a credit card becomes a user and the type of transaction becomes an item. The type of transaction is represented by MCC code (Merchant Code) of the store where a user bought something.


In [4]:
dfMerchant.columns = ['merchant_id', 'merchant_category_id', 'subsector_description', "merchant_latitude", "merchant_longitude"]
dfChd.columns = ['card_id', 'first_active_month', 'reward_program', 'chd_latitude', "chd_longitude", "fico_score", "age"]

In [5]:
#profileMarchant = dfMerchant.profile_report(title = 'Merchant Report', progress_bar=True, infer_dtypes=True)
#profileTrx2018 = dfTrx2018.profile_report(title = 'Transaction 2018 Report', progress_bar=True, infer_dtypes=True)
#profileTrx2017 = dfTrx2017.profile_report(title = 'Transactions 2017 Report', progress_bar=True, infer_dtypes=True)
#profileChd = dfChd.profile_report(title = 'Cardholder Report', progress_bar=True, infer_dtypes=True)
#profileTrx= dfTrx.profile_report(title = 'Transactions', progress_bar=True, infer_dtypes=True)

#profileMarchant.to_file("profileMarchant.html")
#profileTrx2018.to_file("profileTrx2018.html")
#profileTrx2017.to_file("profileTrx2017.html")
#profileTrx.to_file("profileTrx.html")
#profileChd.to_file("profileChd.html")

#profileMarchant.to_notebook_iframe()
#profileTrx2018.to_notebook_iframe()
#profileTrx2017.to_notebook_iframe()
#profileChd.to_notebook_iframe()
#profileTrx.to_notebook_iframe()


In [6]:
def to_float(x):
    try:
        x = float(x)
    except: 
        x = np.nan
    return x

dfTrx['transaction_id'] = dfTrx['transaction_id'].apply(to_float)
dfTrx['authorized_flag'] = dfTrx['authorized_flag'].apply(lambda x: 0.0 if pd.isnull(x) else x )
dfTrx['purchase_date'] = pd.to_datetime(dfTrx['purchase_date'], errors='coerce')
dfTrx['purchase_year'] = dfTrx['purchase_date'].apply(lambda x: str(x).split('-')[0] if x != np.nan else np.nan)
dfTrx['label'] = dfTrx['purchase_date'].apply(lambda x: "predict" if x > BASE_SPLIT_POINT else 'hist')

In [7]:
dfTrx.head()

transaction_id  authorized_flag       purchase_date          card_id  \
0          1000.0              1.0 2017-01-01 00:00:59  C_ID_efced389a0   
1          1001.0              1.0 2017-01-01 00:21:40  C_ID_7aa87f8d62   
2          1002.0              1.0 2017-01-01 00:39:57  C_ID_be5f4e17d9   
3          1003.0              1.0 2017-01-01 00:54:29  C_ID_26cfd3ac01   
4          1004.0              1.0 2017-01-01 00:58:34  C_ID_d51ec5b2a2   

       merchant_id  merchant_category_id item_category  purchase_amount  \
0  M_ID_18038b5ae7                   695             A           194.88   
1  M_ID_a1db5a120b                   198             D           157.81   
2  M_ID_98b342c0e3                   580             A            10.33   
3  M_ID_6d1e255b72                   195             C            69.71   
4  M_ID_7d5f54f2d4                   307             D            50.45   

   signature_provided purchase_year label  
0                   1          2017  hist  
1                   0          2017  hist  
2                   0          2017  hist  
3                   0          2017  hist  
4                   0          2017  hist

In [8]:
df = pd.merge(dfTrx, dfMerchant, on = ['merchant_id', 'merchant_category_id'])
df = pd.merge(df, dfChd, on = "card_id")

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 324032 entries, 0 to 324031
Data columns (total 20 columns):
 #   Column                 Non-Null Count   Dtype         
---  ------                 --------------   -----         
 0   transaction_id         324032 non-null  float64       
 1   authorized_flag        324032 non-null  float64       
 2   purchase_date          324032 non-null  datetime64[ns]
 3   card_id                324032 non-null  object        
 4   merchant_id            324032 non-null  object        
 5   merchant_category_id   324032 non-null  int64         
 6   item_category          324032 non-null  object        
 7   purchase_amount        324032 non-null  float64       
 8   signature_provided     324032 non-null  int64         
 9   purchase_year          324032 non-null  object        
 10  label                  324032 non-null  object        
 11  subsector_description  324032 non-null  object        
 12  merchant_latitude      324032 non-null  floa

In [10]:
df.head()

transaction_id  authorized_flag       purchase_date          card_id  \
0          1000.0              1.0 2017-01-01 00:00:59  C_ID_efced389a0   
1         67121.0              1.0 2017-05-21 19:02:27  C_ID_efced389a0   
2        145446.0              1.0 2017-09-13 11:26:40  C_ID_efced389a0   
3         25841.0              1.0 2017-03-01 20:18:33  C_ID_efced389a0   
4          1774.0              1.0 2017-01-03 22:26:22  C_ID_efced389a0   

       merchant_id  merchant_category_id item_category  purchase_amount  \
0  M_ID_18038b5ae7                   695             A           194.88   
1  M_ID_3111c6df35                   119             B           446.68   
2  M_ID_3111c6df35                   119             B           656.85   
3  M_ID_29ec8d2ab8                   108             D           854.13   
4  M_ID_c6ca6282e6                   818             A           210.93   

   signature_provided purchase_year label subsector_description  \
0                   1          2017  hist                   gas   
1                   0          2017  hist             insurance   
2                   0          2017  hist             insurance   
3                   0          2017  hist                   gas   
4                   0          2017  hist        semiconductors   

   merchant_latitude  merchant_longitude first_active_month reward_program  \
0             40.429             -79.981            2016-12      cash_back   
1             40.413             -79.982            2016-12      cash_back   
2             40.413             -79.982            2016-12      cash_back   
3             40.402             -79.989            2016-12      cash_back   
4             43.219             -71.535            2016-12      cash_back   

   chd_latitude  chd_longitude  fico_score  age  
0        44.686        -72.524         839   18  
1        44.686        -72.524         839   18  
2        44.686        -72.524         839   18  
3        44.686        -72.524         839   18  
4        44.686        -72.524         839   18

In [11]:
profileDf= df.profile_report(title = 'Transactions', progress_bar=True, infer_dtypes=True)
profileDf.to_file("profile.html")
profileDf.to_notebook_iframe()

Summarize dataset:   0%|          | 0/33 [00:00<?, ?it/s]

/home/minty/anaconda3/lib/python3.8/site-packages/scipy/stats/stats.py:4594: RuntimeWarning: overflow encountered in long_scalars
  (2 * xtie * ytie) / m + x0 * y0 / (9 * m * (size - 2)))


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [12]:
df.info()



<class 'pandas.core.frame.DataFrame'>
Int64Index: 324032 entries, 0 to 324031
Data columns (total 20 columns):
 #   Column                 Non-Null Count   Dtype         
---  ------                 --------------   -----         
 0   transaction_id         324032 non-null  float64       
 1   authorized_flag        324032 non-null  float64       
 2   purchase_date          324032 non-null  datetime64[ns]
 3   card_id                324032 non-null  object        
 4   merchant_id            324032 non-null  object        
 5   merchant_category_id   324032 non-null  int64         
 6   item_category          324032 non-null  object        
 7   purchase_amount        324032 non-null  float64       
 8   signature_provided     324032 non-null  int64         
 9   purchase_year          324032 non-null  object        
 10  label                  324032 non-null  object        
 11  subsector_description  324032 non-null  object        
 12  merchant_latitude      324032 non-null  floa

## Simple Recommender
The idea here is to compute, the "baseline recommender". So essentially we are computing the most popular products taking into the account amount and frequency.
1. define metric, to compute score (collab between # trx and avg amount)
1. decide on prerequiste (exclude below 80 %, certain geo location, etx)
1. calculate score for every mcc
1. sort mcc based on the score

In [13]:
# prepare new df for MCC (kind of a product)
dfMerchant.head()
dfSR = df.groupby(['merchant_id']).aggregate({'transaction_id': 'count',
                             'purchase_amount': 'sum'})
dfSR.columns = [ 'trx_cnt', "total_amount"]
dfSRMerch = pd.merge(dfSR, dfMerchant, on = ['merchant_id'])
dfSRMerch.head()

merchant_id  trx_cnt  total_amount  merchant_category_id  \
0  M_ID_0000edb21f        1        138.63                   422   
1  M_ID_0000fd7caf        3        261.27                   557   
2  M_ID_0002237144        3        133.53                   171   
3  M_ID_00037f6a5d        5       1285.11                    68   
4  M_ID_0003f1b272        1        302.76                   278   

  subsector_description  merchant_latitude  merchant_longitude  
0  consumer electronics             41.803             -72.660  
1        retail apparel             43.223             -71.518  
2                   gas             43.172             -71.593  
3  consumer electronics             42.646             -73.758  
4     restaurant/dining             44.191             -73.848

In [14]:
#Only consider MCC in certain geo location
#dfSRMerch = dfSRMerch[(dfSRMerch['merchant_latitude'] >= 45) & (df['merchant_longitude'] <= 300)]

#Only consider MCC that more than 20 trx
dfSRMerch = dfSRMerch[dfSRMerch['trx_cnt'] >= 20]
#Calculate 80th percentile mcc
m = dfSRMerch['total_amount'].quantile(0.80)
dfSRMerch.shape
C = dfSRMerch['trx_cnt'].mean()

def weighted_rating(x, m=m, C=C):
    v = x['trx_cnt']
    R = x['total_amount']
    # Compute the weighted score
    return (v/(v+m) * R) + (m/(m+v) * C)

dfSRMerch['score'] = dfSRMerch.apply(weighted_rating, axis=1)
dfSRMerch.head()

merchant_id  trx_cnt  total_amount  merchant_category_id  \
5    M_ID_0003f9a7c4       22       3774.58                   289   
32   M_ID_001d92b649      211      46602.82                   889   
70   M_ID_0041b721d8       27      16920.34                   796   
78   M_ID_004995eae1      192      40513.72                   299   
113  M_ID_0074dd7c6e       66      31985.17                   333   

    subsector_description  merchant_latitude  merchant_longitude       score  
5    consumer electronics             42.220             -71.813   80.759823  
32   consumer electronics             42.678             -73.782  658.063776  
70              insurance             41.793             -72.693  103.147966  
78           luxury goods             41.720             -72.711  536.827929  
113             insurance             42.630             -73.716  201.854812

In [15]:
#Sort mcc in descending order of their scores
dfSRMerch = dfSRMerch.sort_values('score', ascending=False)

#Print the top 25 mcc
dfSRMerch.head(25)

merchant_id  trx_cnt  total_amount  merchant_category_id  \
172    M_ID_00a6ca8a8a    17064    3582322.73                   879   
22348  M_ID_50f575c681     2877    1541715.70                   796   
62686  M_ID_e5374dabc0     6845     224992.42                   130   
18898  M_ID_445742726b     1049     529247.40                   119   
13462  M_ID_3111c6df35      814     654052.01                   119   
56177  M_ID_cd2c0b07e9     1516     252277.07                   130   
68019  M_ID_f86439cec0     1704     147713.42                   195   
69147  M_ID_fc7d7969c3     2709      95513.59                   401   
10479  M_ID_2637773dd2     1045     193850.95                   422   
24715  M_ID_59764e8cb1      592     311364.88                   755   
50973  M_ID_b9dcf28cb9     1123     168107.90                   401   
27650  M_ID_6464db3b45      340     477669.71                   119   
46568  M_ID_a9d91682ad      767     174728.30                   506   
42048  M_ID_98b342c0e3     1492      77600.84                   580   
55403  M_ID_ca4d18b336      408     228996.17                   108   
60905  M_ID_deb43ff012      669     125358.51                   889   
49791  M_ID_b5b80addf5      679     107820.27                   401   
19948  M_ID_48257bb851      640     106544.84                   497   
35968  M_ID_82a30d9203     1000      69063.00                   695   
35799  M_ID_820c7b73c8      702      91255.49                   248   
51009  M_ID_b9f9332438      386     161974.15                   357   
59216  M_ID_d86b8cc0eb      567     110337.04                   126   
43549  M_ID_9e84cda3b1      462     125940.16                   884   
2083   M_ID_076cd8a829      215     227598.42                   695   
10646  M_ID_26d4fadb60     1035      43130.17                   416   

      subsector_description  merchant_latitude  merchant_longitude  \
172                     gym             42.273             -71.797   
22348             insurance             41.718             -72.722   
62686          luxury goods             43.218             -71.526   
18898             insurance             42.241             -71.813   
13462             insurance             40.413             -79.982   
56177          luxury goods             40.387             -80.029   
68019                   gas             42.230             -71.822   
69147          luxury goods             42.217             -71.765   
10479  consumer electronics             43.226             -71.544   
24715              internet             44.613             -70.230   
50973          luxury goods             41.733             -73.974   
27650             insurance             40.465             -80.027   
46568                dental             43.578             -72.429   
42048              internet             43.177             -71.547   
55403                   gas             42.286             -71.758   
60905  consumer electronics             40.480             -80.030   
49791          luxury goods             42.623             -73.798   
19948  consumer electronics             43.198             -71.584   
35968                   gas             41.706             -73.952   
35799              internet             43.257             -74.231   
51009  consumer electronics             43.219             -71.534   
59216  consumer electronics             40.396             -80.031   
43549  consumer electronics             43.232             -71.515   
2083                    gas             42.218             -71.760   
10646              internet             43.180             -71.554   

              score  
172    1.813104e+06  
22348  2.271930e+05  
62686  6.559807e+04  
18898  3.143631e+04  
13462  3.055489e+04  
56177  2.112078e+04  
68019  1.378141e+04  
69147  1.342979e+04  
10479  1.151842e+04  
24715  1.076287e+04  
50973  1.069210e+04  
27650  9.632434e+03  
46568  7.766383e+03  
42048  6.450951e+03  
55403  5.5507

## Collaborative filtering
1. get data
1. compute a representation to be used for similarity scoring (TF IDF of the desc)
1. Compute cosine similarity between each mcc (will use dot product)
4. Write recommender function

In [16]:
# prepare new df for MCC (kind of a product)
#dfCFMerch = dfMerchant
#dfCFMerch = dfCFMerch.set_index('merchant_id')
#dfCFMerch = dfCFMerch.drop(columns=['merchant_latitude', 'merchant_longitude', 'merchant_category_id'])
#dfCFMerch.info()

dfCFMerch = dfSRMerch
dfCFMerch.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1960 entries, 172 to 43112
Data columns (total 8 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   merchant_id            1960 non-null   object 
 1   trx_cnt                1960 non-null   int64  
 2   total_amount           1960 non-null   float64
 3   merchant_category_id   1960 non-null   int64  
 4   subsector_description  1960 non-null   object 
 5   merchant_latitude      1960 non-null   float64
 6   merchant_longitude     1960 non-null   float64
 7   score                  1960 non-null   float64
dtypes: float64(4), int64(2), object(2)
memory usage: 137.8+ KB


In [17]:
# In this case Term Freqency - Inverse Document Frequency is an overkill
# just want to try it out
from sklearn.feature_extraction.text import TfidfVectorizer
tfidf = TfidfVectorizer(stop_words='english')
dfCFMerch['subsector_description'] = dfCFMerch['subsector_description'].fillna('')
tfidf_matrix = tfidf.fit_transform(dfCFMerch['subsector_description'])
tfidf_matrix.shape
#tfidf_matrix.data[1:20]
#tfidf_matrix.indices

(1960, 31)

In [18]:
# Compute the cosine similarity matrix
from sklearn.metrics.pairwise import linear_kernel
sim = linear_kernel(tfidf_matrix, tfidf_matrix)

In [19]:
#print(f"dfCFMerch.shape {dfCFMerch.shape}")
#print(f"dfMerchant.shape {dfMerchant.shape}")

In [20]:
indices = pd.Series(dfCFMerch.index, index=dfCFMerch['merchant_id']).drop_duplicates()

In [21]:
# Take an MCC code and provide 10 similar
def recommender(merchant_id, sim=sim, df=dfCFMerch, indices=indices):
    # Obtain the index of the movie that matches the title
    idx = indices[merchant_id]
    sim_scores = list(enumerate(sim[idx]))
    sim_scores = sorted(sim_scores, key=lambda x: x[1], reverse=True)
    sim_scores = sim_scores[0:11]
    mcc_indices = [i[0] for i in sim_scores]

    # Return the top 10 most similar movies
    return df.iloc[mcc_indices]

In [22]:
#try out a sample MCC, and we see that products(merchangs in the same subsector)
recommender('M_ID_00a6ca8a8a')

merchant_id  trx_cnt  total_amount  merchant_category_id  \
24715  M_ID_59764e8cb1      592     311364.88                   755   
42048  M_ID_98b342c0e3     1492      77600.84                   580   
35799  M_ID_820c7b73c8      702      91255.49                   248   
10646  M_ID_26d4fadb60     1035      43130.17                   416   
30647  M_ID_6f274b9340     1152      38034.07                   416   
66237  M_ID_f2045dd267      443      74678.00                   755   
7392   M_ID_1ac6bbc867      651      35675.23                   179   
40733  M_ID_940fb4498f      743      27243.97                   580   
53529  M_ID_c355870ab2      321      49663.76                   580   
17461  M_ID_3f644b8667      305      47887.21                   580   
54556  M_ID_c6ffe460d4      191      67216.34                   416   

      subsector_description  merchant_latitude  merchant_longitude  \
24715              internet             44.613             -70.230   
42048              internet             43.177             -71.547   
35799              internet             43.257             -74.231   
10646              internet             43.180             -71.554   
30647              internet             42.306             -71.765   
66237              internet             43.207             -71.508   
7392               internet             42.612             -73.723   
40733              internet             41.664             -73.916   
53529              internet             41.713             -72.662   
17461              internet             40.417             -80.017   
54556              internet             40.405             -80.032   

              score  
24715  10762.873877  
42048   6450.950894  
35799   3764.324572  
10646   2595.357279  
30647   2531.992051  
66237   2009.156097  
7392    1415.277870  
40733   1236.343222  
53529   1013.722731  
17461    935.862648  
54556    837.268484

In [23]:
#User Based Collaborative Filter using Mean Ratings
def cf_user_mean(card_id, merchant_category_id):
    
    if merchant_category_id in r_matrix:
        mean_rating = dfSummary[merchant_category_id].mean()   
    else:
        mean_rating = dfTrx["purchase_amount"].mean()    
    return mean_rating

# Matrix factorization
## PCA

In [24]:
Image(url="https://miro.medium.com/max/3630/1*E9EE5LXxty1EB8fn_s1jkQ@2x.png")

In [25]:
dfSummary = pd.pivot_table(df, index='card_id', columns='merchant_category_id', values='purchase_amount', aggfunc='sum', fill_value=0)
dfSummary.head(8)


merchant_category_id  2    9    14   16   19   21   33   34   36   38   ...  \
card_id                                                                 ...   
C_ID_0002709b5a       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_0004725b87       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_0006152db8       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_00079fec55       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_0007a60a33       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_0007fe3157       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_0009d25138       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
C_ID_000acab1f6       0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   

merchant_category_id  843  847  854  873  879  881     884  885  889  891  
card_id                                                                    
C_ID_0002709b5a       0.0  0.0  0.0  0.0  0.0  0.0  384.75  0.0  0.0  0.0  
C_ID_0004725b87       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_0006152db8       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_00079fec55       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_0007a60a33       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_0007fe3157       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_0009d25138       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  
C_ID_000acab1f6       0.0  0.0  0.0  0.0  0.0  0.0    0.00  0.0  0.0  0.0  

[8 rows x 270 columns]

In [26]:
features = StandardScaler().fit_transform(dfSummary)
pca = PCA(n_components=.6, whiten=True)
features_pca = pca.fit_transform(features)
print("Original number of features", features.shape[1])
print("Reduced number of features", features_pca.shape[1])

Original number of features 270
Reduced number of features 149


## Matrix Factorization using Truncated SVD

In [27]:
from sklearn.decomposition import TruncatedSVD
from scipy.sparse import csr_matrix

features = StandardScaler().fit_transform(dfSummary)

features_sparse = csr_matrix(features)
tsvd = TruncatedSVD(n_components=149)
features_sparse_tsvd = tsvd.fit(features_sparse).transform(features_sparse)

print("Original number of features", features_sparse.shape[1])
print("Reduced number of features", features_sparse_tsvd.shape[1])


Original number of features 270
Reduced number of features 149


In [28]:
print(tsvd.explained_variance_ratio_.sum()) 
print(tsvd.explained_variance_ratio_) 

0.5903981849655826
[0.00832808 0.00697901 0.00617386 0.00577632 0.00550441 0.00505668
 0.0049995  0.00485166 0.00482045 0.00473174 0.0046336  0.00461182
 0.00453189 0.00450818 0.00445592 0.00442209 0.00440735 0.00438246
 0.00436683 0.00434991 0.00432175 0.00431108 0.00428232 0.00427308
 0.00425301 0.00423413 0.00420169 0.00419289 0.00418198 0.00417039
 0.00414438 0.00414364 0.00411303 0.00409454 0.00408579 0.00407857
 0.00405938 0.00405348 0.00403518 0.00402489 0.00401589 0.00399753
 0.00399049 0.00398312 0.0039687  0.00396238 0.00395201 0.00394526
 0.00393903 0.00393448 0.00391688 0.00391285 0.00390048 0.00389779
 0.00388805 0.00388476 0.00388026 0.00386432 0.00386009 0.00385617
 0.00384243 0.00383979 0.00383376 0.00382667 0.00381459 0.0038124
 0.00381167 0.00380183 0.00379824 0.00379605 0.00379244 0.0037821
 0.00377482 0.00377088 0.0037659  0.00376364 0.00375824 0.00375656
 0.00375458 0.00374703 0.00374553 0.00374417 0.00373856 0.00373485
 0.00373059 0.00372783 0.0037245  0.00371982 

# Next Steps
* remove anamoly
* look at the time dimension
* try the supervised approach from here https://github.com/datagym-ru/retailhero-recomender-baseline/blob/master/src/train_valid_split.py